# **Bitcoin price forecasting - GBTRegressor**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author
Corsi Danilo - corsi.1742375@studenti.uniroma1.it



## Global constants, dependencies, libraries and tools

In [1]:
# GDrive root
GDRIVE_DIR = "/content/drive"

# Dataset
GDRIVE_DATASET_OUTPUT_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/datasets/output"
GDRIVE_DATASET_NAME = "bitcoin_blockchain_data_30min"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_NAME + "_train_valid"
GDRIVE_DATASET_NAME_EXT_ENG  = "/" + GDRIVE_DATASET_NAME_ENG + ".parquet"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_OUTPUT_DIR + GDRIVE_DATASET_NAME_EXT_ENG

# Features
GDRIVE_FEATURES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/features"
GDRIVE_ALL_FEATURES_NAME = "all_features"
GDRIVE_MORE_REL_FEATURES_NAME = "more_rel_features"
GDRIVE_LESS_REL_FEATURES_NAME = "less_rel_features"
GDRIVE_ALL_FEATURES_NAME_EXT = "/" + GDRIVE_ALL_FEATURES_NAME + ".json"
GDRIVE_MORE_REL_FEATURES_NAME_EXT = "/" + GDRIVE_MORE_REL_FEATURES_NAME + ".json"
GDRIVE_LESS_REL_FEATURES_NAME_EXT = "/" + GDRIVE_LESS_REL_FEATURES_NAME + ".json"
GDRIVE_ALL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_ALL_FEATURES_NAME_EXT
GDRIVE_MORE_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_MORE_REL_FEATURES_NAME_EXT
GDRIVE_LESS_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_LESS_REL_FEATURES_NAME_EXT

# Others
JAVA_HOME = "/usr/lib/jvm/java-8-openjdk-amd64"
MODEL_NAME = "GBTRegressor"
SLOW_OPERATION = True

In [2]:
# Point Colaboratory to our Google Drive
from google.colab import drive

# Define GDrive paths
drive.mount(GDRIVE_DIR, force_remount=True)

Mounted at /content/drive


In [3]:
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

In [4]:
# Install Spark and related dependencies
!pip install pyspark

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.8/310.8 MB 4.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.4.1-py2.py3-none-any.whl size=311285388 sha256=2fc6ee35697c7851a48101b56b93f95a2582d15c378126b21f28ffbc4a3a872a
  Stored in directory: /root/.cache/pip/wheels/0d/77/a3/ff2f74cc9ab41f8f594dabf0579c2a7c6de920d584206e0834
Successfully built pyspark


## Import files

In [5]:
GDRIVE_UTILITIES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/utilities"

import sys
sys.path.append(GDRIVE_UTILITIES_DIR)

from imports import *
import utilities, parameters

importlib.reload(utilities)
importlib.reload(parameters)

<module 'parameters' from '/content/drive/MyDrive/BDC/project/utilities/parameters.py'>

## Create the pyspark session

In [6]:
# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '4G').\
                set('spark.driver.memory', '45G').\
                set('spark.driver.maxResultSize', '10G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPriceForecasting").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

## Loading dataset

In [7]:
# Load datasets into pyspark dataset objects
df = spark.read.load(GDRIVE_DATASET_NAME_ENG,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

In [8]:
def dataset_info(dataset):
  dataset.show(3)

  # Get the number of rows
  num_rows = dataset.count()

  # Get the number of columns
  num_columns = len(dataset.columns)

  # Print the shape of the dataset
  print("Shape:", (num_rows, num_columns))

  # Print the schema of the dataset
  dataset.printSchema()

In [9]:
if SLOW_OPERATION:
  dataset_info(df)

+-------------------+---+------------------+--------------+-------------------+--------------+------------------+------------------+--------------------+------------------------+-----------------+-------------------+------------------+--------------------+------------------+------------------+--------------------------------+--------------------+------------------+------------------+------------------+------------------+------------------+------------------+
|          timestamp| id|      market-price|total-bitcoins|         market-cap|  trade-volume|       blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|        hash-rate|         difficulty|    miners-revenue|transaction-fees-usd|n-unique-addresses|    n-transactions|estimated-transaction-volume-usd|      rate-of-change|        sma-5-days|        sma-7-days|       sma-10-days|       sma-20-days|       sma-50-days|      sma-100-days|
+-------------------+---+------------------+--------------+---------------

## Loading features

In [10]:
# Set the features label
FEATURES_LABEL = "features"

# Set the target variable
TARGET_VAL = 'market-price'

In [11]:
# Loading correlation matrix features
with open(GDRIVE_ALL_FEATURES, "r") as f:
    all_features = json.load(f)
print(all_features)

['total-bitcoins', 'market-cap', 'trade-volume', 'blocks-size', 'avg-block-size', 'n-transactions-total', 'n-transactions-per-block', 'hash-rate', 'difficulty', 'miners-revenue', 'transaction-fees-usd', 'n-unique-addresses', 'n-transactions', 'estimated-transaction-volume-usd', 'rate-of-change', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'sma-20-days', 'sma-50-days', 'sma-100-days']


In [12]:
# Loading correlation matrix features
with open(GDRIVE_MORE_REL_FEATURES, "r") as f:
    more_rel_features = json.load(f)
print(more_rel_features)

['market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'estimated-transaction-volume-usd', 'sma-10-days', 'n-transactions-total', 'blocks-size', 'sma-100-days', 'total-bitcoins']


In [13]:
# Loading correlation matrix features
with open(GDRIVE_LESS_REL_FEATURES, "r") as f:
    less_rel_features = json.load(f)
print(less_rel_features)

['sma-20-days', 'sma-50-days', 'n-unique-addresses', 'difficulty', 'hash-rate', 'avg-block-size', 'transaction-fees-usd', 'trade-volume', 'n-transactions-per-block', 'n-transactions', 'rate-of-change']


## Simple model

In [ ]:
# Get default params
params = parameters.get_defaults_model_params(MODEL_NAME)
params

{'maxIter': [20], 'maxDepth': [5], 'stepSize': [0.1]}

In [ ]:
# Valid performances with all the features
simple_res_all, simple_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_all

Model    Type      Features    Parameters         RMSE      MAPE  \
0  GBTRegressor  simple  all_features  [20, 5, 0.1]  3801.099853  0.143317   

           MAE      Variance        R2  Adjusted_R2       Time  
0  2985.507071  2.653492e+07 -0.578428    -0.579049  13.982678

In [ ]:
utilities.show_results(simple_pred_all, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_res_more_rel, simple_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_more_rel

Model    Type           Features    Parameters         RMSE  \
0  GBTRegressor  simple  more_rel_features  [20, 5, 0.1]  4247.845509   

       MAPE          MAE      Variance        R2  Adjusted_R2       Time  
0  0.161445  3365.379551  3.084828e+07 -0.971258    -0.972034  12.472383

In [ ]:
utilities.show_results(simple_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_res_less_rel, simple_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_less_rel

Model    Type           Features    Parameters          RMSE  \
0  GBTRegressor  simple  less_rel_features  [20, 5, 0.1]  17719.013258   

     MAPE           MAE      Variance         R2  Adjusted_R2      Time  
0  0.7482  14847.970878  3.120252e+08 -33.299292   -33.312792  12.94392

In [ ]:
utilities.show_results(simple_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Simple model (with data normalization)

In [ ]:
# Valid performances with all the features
simple_norm_res_all, simple_norm_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_all

Model         Type      Features    Parameters         RMSE  \
0  GBTRegressor  simple_norm  all_features  [20, 5, 0.1]  9233.792812   

       MAPE          MAE      Variance        R2  Adjusted_R2       Time  
0  0.370421  7872.460089  8.663781e+07 -8.314646    -8.319046  14.503639

In [ ]:
utilities.show_results(simple_norm_pred_all, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_norm_res_more_rel, simple_norm_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_more_rel

Model         Type           Features    Parameters         RMSE  \
0  GBTRegressor  simple_norm  more_rel_features  [20, 5, 0.1]  2507.286094   

      MAPE          MAE      Variance        R2  Adjusted_R2       Time  
0  0.10184  2074.806976  1.294767e+07  0.313226     0.312902  13.337561

In [ ]:
utilities.show_results(simple_norm_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_norm_res_less_rel, simple_norm_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_less_rel

Model         Type           Features    Parameters          RMSE  \
0  GBTRegressor  simple_norm  less_rel_features  [20, 5, 0.1]  12785.977418   

       MAPE           MAE      Variance         R2  Adjusted_R2       Time  
0  0.605254  11907.623234  1.564686e+08 -16.859691   -16.868128  12.438513

In [ ]:
utilities.show_results(simple_norm_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Hyperparameter tuning

In [ ]:
choosen_features = all_features
CHOSEN_FEATURES_LABEL = GDRIVE_ALL_FEATURES_NAME

In [ ]:
# Split proportion list
PORTION_LIST = [0.6, 0.7, 0.8, 0.9]

In [ ]:
# Get simple params
params = parameters.get_model_params(MODEL_NAME)
params

{'maxIter': [10, 20, 30], 'maxDepth': [3, 5, 8], 'stepSize': [0.1, 0.5, 0.7]}

In [ ]:
hyp_res, hyp_params = utilities.autoTuning(df, choosen_features, params, CHOSEN_FEATURES_LABEL, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res

Model        Type      Features  Proportion    Parameters  \
0  GBTRegressor  autotuning  all_features         0.9  [30, 8, 0.7]   

         RMSE      MAPE          MAE      Variance        R2  Adjusted_R2  \
0  6005.16557  0.235885  5042.585018  3.634194e+07 -2.939636    -2.941497   

        Time  
0  32.009007

## Cross validation

In [ ]:
# Get tuned params
params = hyp_params
params

{'maxIter': [30], 'maxDepth': [8], 'stepSize': [0.7]}

In [ ]:
## Cross Validation Parameter
# Multiple Splits Time Series Cross Validation
mul_cv = {'cv_type':'mulTs',
          'kSplits': 5}

# Blocked Time Series Cross Validation
blk_cv = {'cv_type':'blkTs',
          'kSplits': 10}

In [ ]:
mul_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, mul_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res

Model   Type      Features  Splits Train&Validation    Parameters  \
0  GBTRegressor  mulTs  all_features       1   (21182, 21181)  [30, 8, 0.7]   
1  GBTRegressor  mulTs  all_features       2   (42363, 21181)  [30, 8, 0.7]   
2  GBTRegressor  mulTs  all_features       3   (63544, 21181)  [30, 8, 0.7]   
3  GBTRegressor  mulTs  all_features       4   (84725, 21181)  [30, 8, 0.7]   
4  GBTRegressor  mulTs  all_features       5  (105906, 21181)  [30, 8, 0.7]   

           RMSE      MAPE           MAE      Variance        R2  Adjusted_R2  \
0   6654.117230  0.669033   5165.397777  2.664645e+07 -1.482363    -1.483067   
1   2440.096463  0.402068   2040.290678  8.218586e+05 -0.123696    -0.124014   
2   4662.181046  0.448880   4210.934953  2.050723e+07 -7.564580    -7.567007   
3  32873.249691  0.672303  30450.136886  9.313299e+08 -5.101479    -5.103208   
4  13429.348702  0.542344  12012.843355  3.174630e+08 -1.171677    -1.172292   

        Time  
0  24.229675  
1  29.575538  
2  29.307193  
3  30.257329  
4  32.952023

In [ ]:
blk_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, blk_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res

Model   Type      Features  Splits Train&Validation    Parameters  \
0  GBTRegressor  blkTs  all_features       1    (10166, 2542)  [30, 8, 0.7]   
1  GBTRegressor  blkTs  all_features       2    (10166, 2542)  [30, 8, 0.7]   
2  GBTRegressor  blkTs  all_features       3    (10166, 2542)  [30, 8, 0.7]   
3  GBTRegressor  blkTs  all_features       4    (10166, 2542)  [30, 8, 0.7]   
4  GBTRegressor  blkTs  all_features       5    (10166, 2542)  [30, 8, 0.7]   
5  GBTRegressor  blkTs  all_features       6    (10166, 2542)  [30, 8, 0.7]   
6  GBTRegressor  blkTs  all_features       7    (10166, 2542)  [30, 8, 0.7]   
7  GBTRegressor  blkTs  all_features       8    (10166, 2542)  [30, 8, 0.7]   
8  GBTRegressor  blkTs  all_features       9    (10166, 2542)  [30, 8, 0.7]   
9  GBTRegressor  blkTs  all_features      10    (10166, 2542)  [30, 8, 0.7]   

           RMSE      MAPE           MAE      Variance        R2  Adjusted_R2  \
0     47.448337  0.069127     40.614324  2.489457e+03 -5.114280    -5.128751   
1    854.513257  0.310523    693.459165  4.821073e+05 -1.700820    -1.707213   
2   4300.594944  0.386821   4102.498606  1.889704e+07 -6.445276    -6.462898   
3    784.913219  0.083413    430.976844  1.680182e+05 -0.638117    -0.641994   
4   1601.786008  0.124418   1391.103669  2.356101e+06 -2.820622    -2.829665   
5   1730.303286  0.232305   1568.046707  2.762929e+06 -2.222759    -2.230387   
6  12563.054317  0.340573  10732.111167  1.165574e+08 -2.241769    -2.249442   
7   9067.323856  0.155890   7790.234442  8.933287e+07 -1.808985    -1.815633   
8   9899.277124  0.351626   7374.725573  5.793027e+07 -3.604085    -3.614982   
9   3051.797861  0.104388   2639.857098  8.767928e+06 -0.644917    -0.648810   

        Time  
0  20.105078  
1  19.325707  
2  19.909633  
3  19.212633  
4  20.711928  
5  20.104205  
6  20.250856  
7  20.247485  
8  20.073960  
9  22.997025

## Comparison table

In [ ]:
# Define what model_info and evaluators in the Model Comparison Table
model_info = ['Model','Type', 'Features', 'Parameters']
evaluator_lst = ['RMSE','MAPE','MAE','Variance','R2','Adjusted_R2','Time']

# The the Cross Validation results would like to compare
comparison_lst = [simple_res_all, simple_res_more_rel, simple_res_less_rel, simple_norm_res_all, simple_norm_res_more_rel, simple_norm_res_less_rel, hyp_res, mul_cv_res, blk_cv_res]

In [ ]:
# Show the Comparison Table
pd.concat([utilities.modelComparison(cv_result, model_info, evaluator_lst) for cv_result in comparison_lst])

Model         Type           Features    Parameters          RMSE  \
0  GBTRegressor       simple       all_features  [20, 5, 0.1]   3801.099853   
0  GBTRegressor       simple  more_rel_features  [20, 5, 0.1]   4247.845509   
0  GBTRegressor       simple  less_rel_features  [20, 5, 0.1]  17719.013258   
0  GBTRegressor  simple_norm       all_features  [20, 5, 0.1]   9233.792812   
0  GBTRegressor  simple_norm  more_rel_features  [20, 5, 0.1]   2507.286094   
0  GBTRegressor  simple_norm  less_rel_features  [20, 5, 0.1]  12785.977418   
0  GBTRegressor   autotuning       all_features  [30, 8, 0.7]   6005.165570   
0  GBTRegressor        mulTs       all_features  [30, 8, 0.7]  12011.798627   
0  GBTRegressor        blkTs       all_features  [30, 8, 0.7]   4390.101221   

       MAPE           MAE      Variance         R2  Adjusted_R2       Time  
0  0.143317   2985.507071  2.653492e+07  -0.578428    -0.579049  13.982678  
0  0.161445   3365.379551  3.084828e+07  -0.971258    -0.972034  12.472383  
0  0.748200  14847.970878  3.120252e+08 -33.299292   -33.312792  12.943920  
0  0.370421   7872.460089  8.663781e+07  -8.314646    -8.319046  14.503639  
0  0.101840   2074.806976  1.294767e+07   0.313226     0.312902  13.337561  
0  0.605254  11907.623234  1.564686e+08 -16.859691   -16.868128  12.438513  
0  0.235885   5042.585018  3.634194e+07  -2.939636    -2.941497  32.009007  
0  0.546925  10775.920730  2.593537e+08  -3.088759    -3.089918  29.264352  
0  0.215908   3676.362759  2.972572e+07  -2.724163    -2.732978  20.293851

## Training the final model

In [15]:
model = utilities.train_final_model(df, choosen_features, params, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)

In [16]:
GDRIVE_MODELS_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/models"
GDRIVE_MODEL_NAME_EXT = GDRIVE_MODELS_DIR + "/" + MODEL_NAME

In [17]:
# Save the trained model
model.write().overwrite().save(GDRIVE_MODEL_NAME_EXT)